In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import copy


In [2]:
data = pd.read_csv("../data/txn_by_dept.csv")
data.head()

POS Txn                       Dept   ID  Sales U
0  16120100160021008773               0261:HOSIERY  250        2
1  16120100160021008773  0634:VITAMINS & HLTH AIDS  102        1
2  16120100160021008773          0879:PET SUPPLIES  158        2
3  16120100160021008773                 0973:CANDY  175        2
4  16120100160021008773               0982:SPIRITS  176        1

In [3]:
depts = set(data['Dept'])
transactions = set(data['POS Txn'])
data["ID"] = data["ID"].astype(str)
ids = set(data["ID"])

In [4]:
print(ids)

{'169', '202', '309', '307', '38', '135', '213', '23', '37', '128', '78', '265', '53', '292', '133', '266', '7', '5', '151', '143', '65', '94', '1', '22', '29', '131', '28', '278', '52', '165', '86', '310', '110', '132', '79', '36', '32', '73', '146', '74', '242', '122', '148', '82', '171', '80', '76', '269', '152', '50', '59', '182', '160', '308', '63', '26', '70', '11', '49', '277', '158', '235', '46', '9', '214', '164', '45', '13', '77', '99', '166', '48', '113', '138', '150', '149', '108', '97', '61', '154', '177', '3', '81', '183', '295', '296', '85', '270', '17', '106', '12', '27', '134', '100', '204', '109', '144', '58', '157', '56', '178', '105', '64', '75', '129', '264', '40', '273', '306', '30', '57', '179', '272', '184', '263', '147', '305', '6', '141', '42', '297', '102', '41', '21', '51', '10', '54', '104', '87', '72', '175', '288', '311', '268', '200', '18', '55', '14', '155', '176', '185', '31', '219', '107', '167', '2', '170', '24', '71', '250', '8', '34', '19', '111', 

In [5]:
adj_matrix = pd.DataFrame(columns = ids, index = transactions, data = np.zeros((len(transactions), len(ids))))
for row in data.iterrows():
    adj_matrix[row[1][2]].loc[row[1][0]] += 1


# mask = adj_matrix>=1
# adj_matrix_binary = adj_matrix.mask(adj_matrix >= 1, 1)
adj_matrix.head()   

169  202  309  307   38  135  213   23   37  128  ...  \
16120100160034005060  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005061  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005062  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005063  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005064  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   

                        8   34   19  111  156   44   60  294   35   93  
16120100160034005060  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005061  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005062  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005063  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005064  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[5 rows x 160 columns]

In [6]:
support = []
relative_support = []
for col in adj_matrix.columns: 
    support.append(adj_matrix[col].sum())
    relative_support.append(adj_matrix[col].sum()/len(adj_matrix))


In [7]:
def get_candidates(k, frequents):
    j = k-1
    candidates = []    
    if k > 1:
#             print('here ', k)
            for f1 in range(len(frequents)):
                for f2 in range(f1+1, len(frequents)):
                    if frequents[f1][0:j]==frequents[f2][0:j]:
#                         print('f1', frequents[f1][0:j+1])
#                         print('f2', frequents[f2][j:])
                        candidates.append(frequents[f1][0:j+1]+frequents[f2][j:])
#             print('candidates:', ca    # just work w    # just work way through by removing one each timeay through by removing one each timendidates)
    else:
        for f1 in range(len(frequents)):
            for f2 in range(f1+1, len(frequents)):
                candidates.append([frequents[f1],frequents[f2]])
    
    return candidates

In [8]:
def frequent_item_sets(adj_matrix, C1_itemset, min_sup):
    support_dict = {}
    binary_matrix = adj_matrix.copy()
    max_itemset = len(C1_itemset)
    candidates = C1_itemset
    
    frequents = []
    supports = []
    for candidate in candidates:
        support = binary_matrix[candidate].sum()
        

        if support >= min_sup:
                frequents.append(candidate)
                supports.append(support)
#                 print(candidate, support)

    if len(frequents) == 0:
        return support_dict

    support_dict[1] = [frequents, supports]
    candidates = get_candidates(1, frequents)
                    
    for k in range(2, max_itemset):
        print(k)
        frequents = []
        supports = []
        for candidate in candidates:
            support = binary_matrix.where(binary_matrix[candidate].sum(axis=1) == len(candidate)).sum().max()
#             support = binary_matrix[candidate].sum()
            if support >= min_sup:
                frequents.append(candidate)
                supports.append(support)
#                 print(candidate, support)

                
        if len(frequents) == 0:
            print('No Frequents')
            return support_dict
        
        support_dict[k] = [frequents, supports]
#         print(frequents)
        
        
        candidates = get_candidates(k, frequents)
#         print('full candidates ', candidates)
        candidates = prune_candidates(candidates, frequents)
#         print('pruned ', candidates)

    return support_dict

In [9]:
def prune_candidates(candidates, frequent_set):
    pruned_list = []
    
    for c in range(len(candidates)):
        prune_flag = False
        for i in range(len(candidates[c])):
#             try:
            temp = copy.deepcopy(candidates[c])
            temp.pop(i)
            if temp not in frequent_set:
                prune_flag = True
                break
        if not prune_flag:
            pruned_list.append(candidates[c])
#             except:
#                 print('candidate ', candidates[c])
#                 print('temp', temp)
#                 print('pruned_list', pruned_list)
    return pruned_list

In [10]:
def get_antecedents(parent_set, frequency_dict, max_key):
    antecedents = []
    for key in frequency_dict.keys():
        if key < max_key:
            f_set = frequency_dict[key]
            print('f_set', list(f_set[0][1]))
#             print('f_set_can', f_set[0])
#             print('f_set_sup', f_set[1])
            for i in range(len(f_set[0])):
                print(f_set[0][i])
                if len(list(f_set[0][i]))==1:
                    temp = [f_set[0][i]]
                else:
                    temp = f_set[0][i]
#                 print(set(temp))
#                 print(set(parent_set))
                if set(temp).issubset(set(parent_set)):
#                     print(temp,f_set[1][i])
                    antecedents.append([temp,f_set[1][i]])
                
        else:
            break
                                        
                    
    return antecedents
                
    

In [11]:
def get_association_rules(frequency_dict, min_conf):
    confidence_dict = []
    for key in frequency_dict.keys():
        if key > 1:
            for i in range(len(frequency_dict[key][0])):
                z = frequency_dict[key][0][i]
                z_sup = frequency_dict[key][1][i]
                print('parent set: ', z, z_sup)
                antecedents = get_antecedents(z, frequency_dict, key)
#                 print('antecedents: ', antecedents)
                
#                 for antecedent in antecedents:
                while len(antecedents) > 0:
                    antecedent = antecedents.pop()
                    x = set(antecedent[0])
                    x_sup = antecedent[1]
                    print('X', x, x_sup)
                    y = set(z)-x
#                     for compliment in antecedents:
#                         if set(compliment[0]) == y:
#                             y_sup = compliment[1]
#                             print('Y', y, y_sup)
                    confidence = z_sup/x_sup
                    print(x, '->', y, confidence)
                    if confidence >= min_conf:
                        confidence_dict.append([list(x),list(y), confidence])
                    else:
                        antecedents = prune_antecedents(x, antecedents)
#                         print('pruned', antecedents)
                            
    return confidence_dict

In [12]:
def prune_antecedents(x, antecedents):
    pruned_antecedents = []
    for antecedent in antecedents:
        if set(antecedent[0]).issubset(x):
            pass
        else:
            pruned_antecedents.append(antecedent)
            
    return pruned_antecedents

In [13]:
def get_evals(confidences_list, frequency_dict, size_dataset):
    metrics = []
    for c in confidences_list:
        print('\n', c)
        confidence = c[2]
        k = len(c[1])
        frequencies = frequency_dict[k]
#         print('frequencies 0', frequencies[0])
#         print('c1', set(c[1]))
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
#             print('temp', temp)
            if set(c[1])==temp:
                support = frequencies[1][i]
        lift = confidence/(support/size_dataset)
        print('lift', lift)
        
        c.append(lift)
        
        # leverage = rel_sup(XY) - rel(x)*rel(y)
        x = set(c[0])
        y = set(c[1])
        xy = x.union(y)
#         print(x)
#         print(y)
#         print(xy)
        k = len(xy)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if xy==temp:
                support_xy = frequencies[1][i]
        rel_xy = support_xy/size_dataset
        
        x = set(c[0])
        k = len(x)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if x==temp:
                support_x = frequencies[1][i]
        rel_x = support_x/size_dataset
        
        y = set(c[1])
        k = len(y)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if y==temp:
                support_y = frequencies[1][i]
        rel_y = support_y/size_dataset
        
        leverage = rel_xy - rel_x*rel_y
        print('leverage', leverage)
        
        c.append(leverage)
        metrics.append([lift, leverage])
        
    return confidences_list, metrics

In [14]:
test1 = [
[1, 0, 1, 1, 0, 0],
[0, 1, 0, 1, 0, 0],
[1, 1, 1, 0, 1, 0],
[0, 1, 0, 1, 0, 1]#,
# [1, 1, 1, 1, 1, 0]
]

test2 = [
[1, 1, 1, 0, 0],
[1, 1, 1, 1, 1],
[1, 0, 1, 1, 0],
[1, 0, 1, 1, 1],
[1, 1, 1, 1, 0]
]

In [15]:
test_df = pd.DataFrame(data=test2, columns = ['A', 'B', 'C', 'D', 'E'])
test_df.head()

A  B  C  D  E
0  1  1  1  0  0
1  1  1  1  1  1
2  1  0  1  1  0
3  1  0  1  1  1
4  1  1  1  1  0

In [16]:
frequent_test = frequent_item_sets(test_df, test_df.columns, 2)
print('\n')
for key in frequent_test.keys():
    print('Item Set Length: ', key, '\n', frequent_test[key][0], '\n', frequent_test[key][1])

2
3
4


Item Set Length:  1 
 ['A', 'B', 'C', 'D', 'E'] 
 [5, 3, 5, 4, 2]
Item Set Length:  2 
 [['A', 'B'], ['A', 'C'], ['A', 'D'], ['A', 'E'], ['B', 'C'], ['B', 'D'], ['C', 'D'], ['C', 'E'], ['D', 'E']] 
 [3.0, 5, 4.0, 2.0, 3.0, 2.0, 4.0, 2.0, 2.0]
Item Set Length:  3 
 [['A', 'B', 'C'], ['A', 'B', 'D'], ['A', 'C', 'D'], ['A', 'C', 'E'], ['A', 'D', 'E'], ['B', 'C', 'D'], ['C', 'D', 'E']] 
 [3.0, 2.0, 4.0, 2.0, 2.0, 2.0, 2.0]
Item Set Length:  4 
 [['A', 'B', 'C', 'D'], ['A', 'C', 'D', 'E']] 
 [2.0, 2.0]


In [17]:
confidence_test = get_association_rules(frequent_test, 1)

parent set:  ['A', 'B'] 3.0
f_set ['B']
A
B
C
D
E
X {'B'} 3
{'B'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'B'} 0.6
parent set:  ['A', 'C'] 5
f_set ['B']
A
B
C
D
E
X {'C'} 5
{'C'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'C'} 1.0
parent set:  ['A', 'D'] 4.0
f_set ['B']
A
B
C
D
E
X {'D'} 4
{'D'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'D'} 0.8
parent set:  ['A', 'E'] 2.0
f_set ['B']
A
B
C
D
E
X {'E'} 2
{'E'} -> {'A'} 1.0
X {'A'} 5
{'A'} -> {'E'} 0.4
parent set:  ['B', 'C'] 3.0
f_set ['B']
A
B
C
D
E
X {'C'} 5
{'C'} -> {'B'} 0.6
X {'B'} 3
{'B'} -> {'C'} 1.0
parent set:  ['B', 'D'] 2.0
f_set ['B']
A
B
C
D
E
X {'D'} 4
{'D'} -> {'B'} 0.5
X {'B'} 3
{'B'} -> {'D'} 0.6666666666666666
parent set:  ['C', 'D'] 4.0
f_set ['B']
A
B
C
D
E
X {'D'} 4
{'D'} -> {'C'} 1.0
X {'C'} 5
{'C'} -> {'D'} 0.8
parent set:  ['C', 'E'] 2.0
f_set ['B']
A
B
C
D
E
X {'E'} 2
{'E'} -> {'C'} 1.0
X {'C'} 5
{'C'} -> {'E'} 0.4
parent set:  ['D', 'E'] 2.0
f_set ['B']
A
B
C
D
E
X {'E'} 2
{'E'} -> {'D'} 1.0
X {'D'} 4
{'D'} -> {'E'} 0.5
parent set:  ['

In [18]:
for c in confidence_test:
    print(c)

[['B'], ['A'], 1.0]
[['C'], ['A'], 1.0]
[['A'], ['C'], 1.0]
[['D'], ['A'], 1.0]
[['E'], ['A'], 1.0]
[['B'], ['C'], 1.0]
[['D'], ['C'], 1.0]
[['E'], ['C'], 1.0]
[['E'], ['D'], 1.0]
[['C', 'B'], ['A'], 1.0]
[['A', 'B'], ['C'], 1.0]
[['B'], ['A', 'C'], 1.0]
[['B', 'D'], ['A'], 1.0]
[['C', 'D'], ['A'], 1.0]
[['A', 'D'], ['C'], 1.0]
[['D'], ['A', 'C'], 1.0]
[['E', 'C'], ['A'], 1.0]
[['E', 'A'], ['C'], 1.0]
[['E'], ['A', 'C'], 1.0]
[['E', 'D'], ['A'], 1.0]
[['E', 'A'], ['D'], 1.0]
[['E'], ['A', 'D'], 1.0]
[['B', 'D'], ['C'], 1.0]
[['E', 'D'], ['C'], 1.0]
[['E', 'C'], ['D'], 1.0]
[['E'], ['C', 'D'], 1.0]
[['C', 'B', 'D'], ['A'], 1.0]
[['A', 'B', 'D'], ['C'], 1.0]
[['B', 'D'], ['A', 'C'], 1.0]
[['E', 'C', 'D'], ['A'], 1.0]
[['E', 'A', 'D'], ['C'], 1.0]
[['E', 'A', 'C'], ['D'], 1.0]
[['E', 'D'], ['A', 'C'], 1.0]
[['E', 'C'], ['A', 'D'], 1.0]
[['E', 'A'], ['C', 'D'], 1.0]
[['E'], ['A', 'C', 'D'], 1.0]


In [19]:
evals = get_lifts(confidence_test, frequent_test, len(test_df))

NameError: name 'get_lifts' is not defined

In [ ]:
for row in evals[0]:
    print(row)

In [20]:
frequent_full = frequent_item_sets(adj_matrix, adj_matrix.columns, 3)

2
3
4
5
6
7
No Frequents


In [21]:
for key in frequent_full.keys():
    print('Item Set Length: ', key, '\n', frequent_full[key])

Item Set Length:  1 
 [['169', '202', '309', '307', '38', '135', '213', '23', '37', '128', '78', '265', '53', '292', '133', '266', '5', '143', '65', '94', '1', '22', '29', '131', '28', '278', '52', '165', '86', '310', '110', '132', '79', '36', '32', '73', '146', '74', '122', '148', '82', '171', '80', '76', '269', '152', '50', '59', '182', '160', '308', '63', '26', '70', '49', '158', '235', '46', '9', '214', '164', '45', '13', '77', '99', '48', '113', '138', '149', '108', '97', '61', '154', '177', '3', '81', '183', '295', '296', '85', '270', '17', '106', '12', '27', '100', '204', '109', '144', '58', '157', '56', '178', '105', '64', '75', '264', '40', '273', '30', '57', '179', '272', '263', '147', '6', '141', '42', '297', '102', '41', '21', '51', '10', '54', '104', '72', '175', '288', '268', '55', '14', '155', '176', '185', '31', '107', '167', '2', '170', '24', '71', '250', '8', '34', '19', '111', '156', '44', '60', '294', '35', '93'], [99.0, 8.0, 7.0, 3.0, 9.0, 8.0, 112.0, 18.0, 6.0, 16

In [22]:
confidence_full = get_association_rules(frequent_full, 1)

parent set:  ['169', '292'] 3.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['169', '143'] 20.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54

204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['265', '72'] 5.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['265', '175'] 4.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9

308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['266', '72'] 3.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['266', '175'] 3.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29


264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['143', '26'] 3.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['143', '70'] 10.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149


122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['143', '147'] 6.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
parent set:  ['143', '42'] 6.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128

...

['160', '72']
['160', '175']
['160', '176']
['160', '24']
['160', '93']
['63', '48']
['63', '60']
['26', '99']
['26', '270']
['26', '175']
['26', '93']
['70', '164']
['70', '99']
['70', '138']
['70', '177']
['70', '296']
['70', '100']
['70', '179']
['70', '72']
['70', '175']
['70', '170']
['70', '93']
['49', '42']
['49', '175']
['158', '99']
['158', '113']
['158', '108']
['158', '154']
['158', '177']
['158', '100']
['158', '178']
['158', '179']
['158', '42']
['158', '102']
['158', '72']
['158', '175']
['158', '176']
['158', '170']
['158', '156']
['158', '60']
['158', '93']
['46', '99']
['46', '177']
['46', '100']
['46', '179']
['46', '42']
['46', '175']
['46', '176']
['46', '170']
['46', '93']
['9', '8']
['164', '296']
['164', '175']
['164', '93']
['45', '99']
['45', '177']
['45', '42']
['45', '175']
['45', '176']
['45', '170']
['13', '175']
['99', '48']
['99', '113']
['99', '138']
['99', '108']
['99', '177']
['99', '81']
['99', '296']
['99', '270']
['99', '106']
['99', '27']
['99', '1

X {'170', '143', '175', '100'} 6.0
{'170', '143', '175', '100'} -> {'169'} 0.5
X {'169', '170', '175', '100'} 5.0
{'169', '170', '175', '100'} -> {'143'} 0.6
X {'169', '170', '143', '175'} 3.0
{'169', '170', '143', '175'} -> {'100'} 1.0
X {'169', '143', '170', '100'} 4.0
{'169', '143', '170', '100'} -> {'175'} 0.75
X {'169', '143', '175', '100'} 4.0
{'169', '143', '175', '100'} -> {'170'} 0.75
parent set:  ['169', '143', '100', '175', '93'] 4.0
f_set ['2', '0', '2']
169
202
309
307
38
135
213
23
37
128
78
265
53
292
133
266
5
143
65
94
1
22
29
131
28
278
52
165
86
310
110
132
79
36
32
73
146
74
122
148
82
171
80
76
269
152
50
59
182
160
308
63
26
70
49
158
235
46
9
214
164
45
13
77
99
48
113
138
149
108
97
61
154
177
3
81
183
295
296
85
270
17
106
12
27
100
204
109
144
58
157
56
178
105
64
75
264
40
273
30
57
179
272
263
147
6
141
42
297
102
41
21
51
10
54
104
72
175
288
268
55
14
155
176
185
31
107
167
2
170
24
71
250
8
34
19
111
156
44
60
294
35
93
f_set ['169', '143']
['169', '292']

['99', '177']
['99', '81']
['99', '296']
['99', '270']
['99', '106']
['99', '27']
['99', '100']
['99', '178']
['99', '179']
['99', '272']
['99', '147']
['99', '6']
['99', '102']
['99', '72']
['99', '175']
['99', '176']
['99', '170']
['99', '24']
['99', '71']
['99', '250']
['99', '294']
['99', '93']
['48', '100']
['48', '42']
['48', '175']
['48', '170']
['48', '60']
['48', '93']
['113', '175']
['113', '170']
['138', '177']
['138', '296']
['138', '179']
['138', '42']
['138', '72']
['138', '175']
['138', '176']
['138', '170']
['138', '24']
['138', '93']
['108', '177']
['108', '100']
['108', '109']
['108', '179']
['108', '147']
['108', '72']
['108', '175']
['108', '176']
['108', '170']
['108', '156']
['108', '60']
['108', '93']
['61', '24']
['61', '60']
['154', '93']
['177', '296']
['177', '270']
['177', '100']
['177', '58']
['177', '178']
['177', '179']
['177', '272']
['177', '6']
['177', '42']
['177', '102']
['177', '41']
['177', '104']
['177', '72']
['177', '175']
['177', '176']
['177',

['170', '156', '93']
f_set ['169', '143', '100', '170']
['169', '143', '100', '175']
['169', '143', '100', '170']
['169', '143', '100', '93']
['169', '143', '175', '170']
['169', '143', '175', '93']
['169', '143', '176', '93']
['169', '143', '170', '93']
['169', '99', '100', '170']
['169', '99', '175', '170']
['169', '99', '170', '93']
['169', '100', '175', '170']
['169', '100', '175', '93']
['169', '100', '170', '93']
['169', '72', '175', '170']
['169', '175', '170', '93']
['143', '94', '175', '93']
['143', '94', '170', '93']
['143', '110', '99', '93']
['143', '26', '99', '93']
['143', '70', '72', '93']
['143', '70', '175', '93']
['143', '158', '99', '93']
['143', '164', '175', '93']
['143', '99', '100', '175']
['143', '99', '100', '93']
['143', '99', '175', '170']
['143', '99', '175', '93']
['143', '99', '71', '93']
['143', '108', '175', '93']
['143', '100', '178', '170']
['143', '100', '178', '93']
['143', '100', '175', '170']
['143', '100', '175', '93']
['143', '100', '176', '170']

['76', '106']
['76', '176']
['269', '270']
['50', '99']
['50', '100']
['50', '51']
['50', '170']
['59', '60']
['160', '158']
['160', '99']
['160', '138']
['160', '177']
['160', '270']
['160', '100']
['160', '178']
['160', '179']
['160', '72']
['160', '175']
['160', '176']
['160', '24']
['160', '93']
['63', '48']
['63', '60']
['26', '99']
['26', '270']
['26', '175']
['26', '93']
['70', '164']
['70', '99']
['70', '138']
['70', '177']
['70', '296']
['70', '100']
['70', '179']
['70', '72']
['70', '175']
['70', '170']
['70', '93']
['49', '42']
['49', '175']
['158', '99']
['158', '113']
['158', '108']
['158', '154']
['158', '177']
['158', '100']
['158', '178']
['158', '179']
['158', '42']
['158', '102']
['158', '72']
['158', '175']
['158', '176']
['158', '170']
['158', '156']
['158', '60']
['158', '93']
['46', '99']
['46', '177']
['46', '100']
['46', '179']
['46', '42']
['46', '175']
['46', '176']
['46', '170']
['46', '93']
['9', '8']
['164', '296']
['164', '175']
['164', '93']
['45', '99']


In [23]:
for c in confidence_full:
    print(c)

[['169', '86'], ['99'], 1.0]
[['169', '70'], ['175'], 1.0]
[['128', '250'], ['175'], 1.0]
[['143', '50'], ['94'], 1.0]
[['51', '143'], ['94'], 1.0]
[['26', '99'], ['143'], 1.0]
[['26', '143'], ['99'], 1.0]
[['26', '93'], ['143'], 1.0]
[['26', '143'], ['93'], 1.0]
[['93', '164'], ['143'], 1.0]
[['143', '71'], ['99'], 1.0]
[['143', '48'], ['93'], 1.0]
[['143', '71'], ['93'], 1.0]
[['50', '100'], ['94'], 1.0]
[['94', '178'], ['100'], 1.0]
[['94', '156'], ['93'], 1.0]
[['176', '110'], ['177'], 1.0]
[['50', '100'], ['51'], 1.0]
[['178', '160'], ['176'], 1.0]
[['26', '93'], ['99'], 1.0]
[['26', '99'], ['93'], 1.0]
[['138', '72'], ['70'], 1.0]
[['70', '138'], ['72'], 1.0]
[['70', '138'], ['175'], 1.0]
[['70', '170'], ['175'], 1.0]
[['93', '164'], ['175'], 1.0]
[['27', '93'], ['99'], 1.0]
[['99', '27'], ['93'], 1.0]
[['138', '72'], ['175'], 1.0]
[['58', '176'], ['177'], 1.0]
[['177', '42'], ['175'], 1.0]
[['177', '102'], ['175'], 1.0]
[['175', '263'], ['72'], 1.0]
[['263', '72'], ['175'], 1.0]

In [24]:
evals_full, m = get_evals(confidence_full, frequent_full, len(adj_matrix))


 [['169', '86'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['169', '70'], ['175'], 1.0]
lift 7.505454545454546
leverage 0.0012598307643771408

 [['128', '250'], ['175'], 1.0]
lift 7.505454545454546
leverage 0.0012598307643771408

 [['143', '50'], ['94'], 1.0]
lift 58.971428571428575
leverage 0.001428841040201911

 [['51', '143'], ['94'], 1.0]
lift 58.971428571428575
leverage 0.001428841040201911

 [['26', '99'], ['143'], 1.0]
lift 13.063291139240507
leverage 0.0013422232738417163

 [['26', '143'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['26', '93'], ['143'], 1.0]
lift 13.063291139240507
leverage 0.0013422232738417163

 [['26', '143'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['93', '164'], ['143'], 1.0]
lift 13.063291139240507
leverage 0.0013422232738417163

 [['143', '71'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['143', '48'], ['93'], 1.0]
lift 10.32
leverage 0.00131264647557

In [25]:
for row in evals_full:
    print(row)

[['169', '86'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['169', '70'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['128', '250'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['143', '50'], ['94'], 1.0, 58.971428571428575, 0.001428841040201911]
[['51', '143'], ['94'], 1.0, 58.971428571428575, 0.001428841040201911]
[['26', '99'], ['143'], 1.0, 13.063291139240507, 0.0013422232738417163]
[['26', '143'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['26', '93'], ['143'], 1.0, 13.063291139240507, 0.0013422232738417163]
[['26', '143'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['93', '164'], ['143'], 1.0, 13.063291139240507, 0.0013422232738417163]
[['143', '71'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['143', '48'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['143', '71'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['50', '100'], ['94'], 1.0, 58.971428571428575, 0.001428841040201911]
[['94', '178'], ['100'], 1.0, 13

In [26]:
for row in m:
    print(row)

[15.518796992481203, 0.0013598285109067965]
[7.505454545454546, 0.0012598307643771408]
[7.505454545454546, 0.0012598307643771408]
[58.971428571428575, 0.001428841040201911]
[58.971428571428575, 0.001428841040201911]
[13.063291139240507, 0.0013422232738417163]
[15.518796992481203, 0.0013598285109067965]
[13.063291139240507, 0.0013422232738417163]
[10.32, 0.0013126464755723814]
[13.063291139240507, 0.0013422232738417163]
[15.518796992481203, 0.0013598285109067965]
[10.32, 0.0013126464755723814]
[10.32, 0.0013126464755723814]
[58.971428571428575, 0.001428841040201911]
[13.578947368421051, 0.0013464485307373355]
[10.32, 0.0013126464755723814]
[10.75, 0.0017577068685776095]
[114.66666666666667, 0.0014408126014061654]
[6.573248407643312, 0.0012323665945556156]
[15.518796992481203, 0.0013598285109067965]
[10.32, 0.0013126464755723814]
[38.943396226415096, 0.0014161652695150531]
[20.038834951456312, 0.0013809547953848927]
[7.505454545454546, 0.0012598307643771408]
[7.505454545454546, 0.0012598